In [1]:
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
from textblob import Word
import re
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics import accuracy_score
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import SGDClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier

data = pd.read_csv('text_emotion.csv')

data = data.drop('author', axis=1)



print(data)

         tweet_id   sentiment  \
0      1956967341       empty   
1      1956967666     sadness   
2      1956967696     sadness   
3      1956967789  enthusiasm   
4      1956968416     neutral   
...           ...         ...   
39995  1753918954     neutral   
39996  1753919001        love   
39997  1753919005        love   
39998  1753919043   happiness   
39999  1753919049        love   

                                                 content  
0      @tiffanylue i know  i was listenin to bad habi...  
1      Layin n bed with a headache  ughhhh...waitin o...  
2                    Funeral ceremony...gloomy friday...  
3                   wants to hang out with friends SOON!  
4      @dannycastillo We want to trade with someone w...  
...                                                  ...  
39995                                   @JohnLloydTaylor  
39996                     Happy Mothers Day  All my love  
39997  Happy Mother's Day to all the mommies out ther...  
39998  @niari

In [2]:
import nltk
nltk.download('vader_lexicon')
from nltk.sentiment.vader import SentimentIntensityAnalyzer
sid = SentimentIntensityAnalyzer()
sentence = "Hello I'm great"
sid.polarity_scores(sentence)

[nltk_data] Downloading package vader_lexicon to
[nltk_data]     /Users/yahya/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


/Users/yahya/anaconda/lib/python3.6/site-packages/nltk/twitter/__init__.py:20: UserWarning: The twython library has not been installed. Some functionality from the twitter package will not be available.
  warnings.warn("The twython library has not been installed. "


{'compound': 0.6249, 'neg': 0.0, 'neu': 0.328, 'pos': 0.672}

In [3]:
from textblob import TextBlob
TextBlob(sentence).sentiment

Sentiment(polarity=0.8, subjectivity=0.75)

In [4]:

import nltk 


In [5]:
nltk.download('twitter_samples')


[nltk_data] Downloading package twitter_samples to
[nltk_data]     /Users/yahya/nltk_data...
[nltk_data]   Package twitter_samples is already up-to-date!


True

In [6]:
import nltk 
from nltk.corpus import twitter_samples

In [7]:
positive_tweets = twitter_samples.strings('positive_tweets.json')
negative_tweets = twitter_samples.strings('negative_tweets.json')
text = twitter_samples.strings('tweets.20150430-223406.json')

In [8]:
print(len(negative_tweets))
negative_tweets

5000


['hopeless for tmr :(',
 "Everything in the kids section of IKEA is so cute. Shame I'm nearly 19 in 2 months :(",
 '@Hegelbon That heart sliding into the waste basket. :(',
 '“@ketchBurning: I hate Japanese call him "bani" :( :(”\n\nMe too',
 'Dang starting next week I have "work" :(',
 "oh god, my babies' faces :( https://t.co/9fcwGvaki0",
 '@RileyMcDonough make me smile :((',
 '@f0ggstar @stuartthull work neighbour on motors. Asked why and he said hates the updates on search :( http://t.co/XvmTUikWln',
 'why?:("@tahuodyy: sialan:( https://t.co/Hv1i0xcrL2"',
 'Athabasca glacier was there in #1948 :-( #athabasca #glacier #jasper #jaspernationalpark #alberta #explorealberta #… http://t.co/dZZdqmf7Cz',
 "I have a really good m&amp;g idea but I'm never going to meet them :(((",
 '@Rampageinthebox mare ivan :(',
 '@SophiaMascardo happy trip, keep safe. see you soon :* :(',
 "I'm so tired hahahah :(",
 '@GrumpyCockney With knee replacements they get you up &amp; about the same day. :-(   Ou

In [9]:
print(len(positive_tweets))
positive_tweets

5000


['#FollowFriday @France_Inte @PKuchly57 @Milipol_Paris for being top engaged members in my community this week :)',
 '@Lamb2ja Hey James! How odd :/ Please call our Contact Centre on 02392441234 and we will be able to assist you :) Many thanks!',
 '@DespiteOfficial we had a listen last night :) As You Bleed is an amazing track. When are you in Scotland?!',
 '@97sides CONGRATS :)',
 'yeaaaah yippppy!!!  my accnt verified rqst has succeed got a blue tick mark on my fb profile :) in 15 days',
 '@BhaktisBanter @PallaviRuhail This one is irresistible :)\n#FlipkartFashionFriday http://t.co/EbZ0L2VENM',
 "We don't like to keep our lovely customers waiting for long! We hope you enjoy! Happy Friday! - LWWF :) https://t.co/smyYriipxI",
 '@Impatientraider On second thought, there’s just not enough time for a DD :) But new shorts entering system. Sheep must be buying.',
 'Jgh , but we have to go to Bayan :D bye',
 'As an act of mischievousness, am calling the ETL layer of our in-house warehousing 

In [10]:
print(len(text))
text

20000


['RT @KirkKus: Indirect cost of the UK being in the EU is estimated to be costing Britain £170 billion per year! #BetterOffOut #UKIP',
 'VIDEO: Sturgeon on post-election deals http://t.co/BTJwrpbmOY',
 'RT @LabourEoin: The economy was growing 3 times faster on the day David Cameron became Prime Minister than it is today.. #BBCqt http://t.co…',
 'RT @GregLauder: the UKIP east lothian candidate looks about 16 and still has an msn addy http://t.co/7eIU0c5Fm1',
 "RT @thesundaypeople: UKIP's housing spokesman rakes in £800k in housing benefit from migrants.  http://t.co/GVwb9Rcb4w http://t.co/c1AZxcLh…",
 'RT @Nigel_Farage: Make sure you tune in to #AskNigelFarage tonight on BBC 1 at 22:50! #UKIP http://t.co/ogHSc2Rsr2',
 'RT @joannetallis: Ed Milliband is an embarrassment. Would you want him representing the UK?!  #bbcqt vote @Conservatives',
 "RT @abstex: The FT is backing the Tories. On an unrelated note, here's a photo of FT leader writer Jonathan Ford (next to Boris) http://t.c…",
 "RT

In [11]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to /Users/yahya/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [12]:
tweet_tokens = twitter_samples.tokenized('positive_tweets.json')
tweet_tokens

[['#FollowFriday',
  '@France_Inte',
  '@PKuchly57',
  '@Milipol_Paris',
  'for',
  'being',
  'top',
  'engaged',
  'members',
  'in',
  'my',
  'community',
  'this',
  'week',
  ':)'],
 ['@Lamb2ja',
  'Hey',
  'James',
  '!',
  'How',
  'odd',
  ':/',
  'Please',
  'call',
  'our',
  'Contact',
  'Centre',
  'on',
  '02392441234',
  'and',
  'we',
  'will',
  'be',
  'able',
  'to',
  'assist',
  'you',
  ':)',
  'Many',
  'thanks',
  '!'],
 ['@DespiteOfficial',
  'we',
  'had',
  'a',
  'listen',
  'last',
  'night',
  ':)',
  'As',
  'You',
  'Bleed',
  'is',
  'an',
  'amazing',
  'track',
  '.',
  'When',
  'are',
  'you',
  'in',
  'Scotland',
  '?',
  '!'],
 ['@97sides', 'CONGRATS', ':)'],
 ['yeaaaah',
  'yippppy',
  '!',
  '!',
  '!',
  'my',
  'accnt',
  'verified',
  'rqst',
  'has',
  'succeed',
  'got',
  'a',
  'blue',
  'tick',
  'mark',
  'on',
  'my',
  'fb',
  'profile',
  ':)',
  'in',
  '15',
  'days'],
 ['@BhaktisBanter',
  '@PallaviRuhail',
  'This',
  'one',
  '

In [13]:
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package wordnet to /Users/yahya/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yahya/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [14]:
from nltk.tag import pos_tag
from nltk.corpus import twitter_samples

tweet_tokens = twitter_samples.tokenized('positive_tweets.json')
print(pos_tag(tweet_tokens[0]))

[('#FollowFriday', 'JJ'), ('@France_Inte', 'NNP'), ('@PKuchly57', 'NNP'), ('@Milipol_Paris', 'NNP'), ('for', 'IN'), ('being', 'VBG'), ('top', 'JJ'), ('engaged', 'VBN'), ('members', 'NNS'), ('in', 'IN'), ('my', 'PRP$'), ('community', 'NN'), ('this', 'DT'), ('week', 'NN'), (':)', 'NN')]


In [15]:
from nltk.tag import pos_tag
from nltk.stem.wordnet import WordNetLemmatizer

def simplifier_phrase(tokens):
    L = WordNetLemmatizer()
    lemmatized_sentence = []
    for mot, tag in pos_tag(tokens):
        if tag.startswith('NN'):
            pos = 'n'
        elif tag.startswith('VB'):
            pos = 'v'
        else:
            pos = 'a'
        lemmatized_sentence.append(L.lemmatize(mot, pos))
    return lemmatized_sentence

print(simplifier_phrase(tweet_tokens[0]))

['#FollowFriday', '@France_Inte', '@PKuchly57', '@Milipol_Paris', 'for', 'be', 'top', 'engage', 'member', 'in', 'my', 'community', 'this', 'week', ':)']


In [16]:
import re, string

def nettoie_donnees(tweet_tokens, stop_words = ()):

    Liste = []

    for mot, tag in pos_tag(tweet_tokens):
        mot = re.sub('http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+#]|[!*\(\),]|'\
                       '(?:%[0-9a-fA-F][0-9a-fA-F]))+','', mot)
        mot = re.sub("(@[A-Za-z0-9_]+)","", mot)

        if tag.startswith("NN"):
            pos = 'n'
        elif tag.startswith('VB'):
            pos = 'v'
        else:
            pos = 'a'

        lemmatizer = WordNetLemmatizer()
        mot = lemmatizer.lemmatize(mot, pos)

        if len(mot) > 0 and mot not in string.punctuation and mot.lower() not in stop_words:
            Liste.append(mot.lower())
    return Liste

In [17]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /Users/yahya/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [18]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

print(nettoie_donnees(tweet_tokens[0], stop_words))

['#followfriday', 'top', 'engage', 'member', 'community', 'week', ':)']


In [19]:
positive_tweet = twitter_samples.tokenized('positive_tweets.json')
negative_tweet = twitter_samples.tokenized('negative_tweets.json')

positive_nettoye = []
negative_nettoye = []

for mot in positive_tweet:
    positive_nettoye.append(nettoie_donnees(mot, stop_words))

for mot in negative_tweet:
    negative_nettoye.append(nettoie_donnees(mot, stop_words))

In [20]:
print(positive_tweet[500])
print(positive_nettoye[500])

['Dang', 'that', 'is', 'some', 'rad', '@AbzuGame', '#fanart', '!', ':D', 'https://t.co/bI8k8tb9ht']
['dang', 'rad', '#fanart', ':d']


In [21]:
def cherche_mots(liste_nettoye):
    for liste in liste_nettoye:
        for mot in liste:
            yield mot

all_words = cherche_mots(positive_nettoye)

In [22]:
from nltk import FreqDist

freq_dist_pos = FreqDist(all_words)
print(freq_dist_pos.most_common(10))

[(':)', 3691), (':-)', 701), (':d', 658), ('thanks', 388), ('follow', 357), ('love', 333), ('...', 290), ('good', 283), ('get', 263), ('thank', 253)]


In [23]:
def prepare_for_model(cleaned_tokens_list):
    for tweet_tokens in cleaned_tokens_list:
        yield dict([token, True] for token in tweet_tokens)

positive_for_model = prepare_for_model(positive_nettoye)
negative_for_model = prepare_for_model(negative_nettoye)

In [24]:
for i in positive_for_model:
    print(i)

{'#followfriday': True, 'top': True, 'engage': True, 'member': True, 'community': True, 'week': True, ':)': True}
{'hey': True, 'james': True, 'odd': True, ':/': True, 'please': True, 'call': True, 'contact': True, 'centre': True, '02392441234': True, 'able': True, 'assist': True, ':)': True, 'many': True, 'thanks': True}
{'listen': True, 'last': True, 'night': True, ':)': True, 'bleed': True, 'amazing': True, 'track': True, 'scotland': True}
{'congrats': True, ':)': True}
{'yeaaaah': True, 'yippppy': True, 'accnt': True, 'verify': True, 'rqst': True, 'succeed': True, 'get': True, 'blue': True, 'tick': True, 'mark': True, 'fb': True, 'profile': True, ':)': True, '15': True, 'day': True}
{'one': True, 'irresistible': True, ':)': True, '#flipkartfashionfriday': True}
{'like': True, 'keep': True, 'lovely': True, 'customer': True, 'wait': True, 'long': True, 'hope': True, 'enjoy': True, 'happy': True, 'friday': True, 'lwwf': True, ':)': True}
{'second': True, 'thought': True, '’': True, 'e

{'sense': True, ':)': True}
{'awww': True, 'pussycats': True, ':-)': True, 'xx': True}
{'hope': True, 'everything': True, 'go': True, 'great': True, ':-)': True, 'lol': True}
{'market': True, 'main': True, 'launch': True, 'pretoria': True, ':)': True}
{'care': True, '...': True, '#fahrinahmad': True, '#tengkuaaronshah': True, '#eksperimencinta': True, ':d': True}
{'tykkäsin': True, 'videosta': True, '200sub': True, 'special': True, '15e': True, 'paysafecard': True, 'giveaway': True, ':)': True, 'lue': True, 'desc': True}
{'2': True, 'month': True, 'wait': True, 'finally': True, 'hoodie': True, ':)': True, 'eeeep': True, 'yay': True, '#sohappyrightnow': True}
{'mmmmmm': True, 'c': True, 'lovely': True, 'azz-sets': True, 'babe': True, ':-)': True}
{'thx': True, 'feedback': True, 'glad': True, 'gain': True, 'value': True, ':)': True}
{'good': True, 'night': True, 'lovely': True, 'hope': True, 'peaceful': True, 'rest': True, 'feel': True, 'refresh': True, 'wake': True, 'sweet': True, 'drea

{"i'll": True, 'add': True, 'fics': True, 'tomorrow': True, ':d': True}
{'#ouch': True, 'slip': True, 'disc': True, 'sore': True, 'today': True, 'bring': True, 'thw': True, 'swimming': True, 'chute': True, ':)': True}
{'morning': True, 'everyone': True, ':d': True}
{'great': True, 'way': True, 'start': True, 'day': True, ':d': True}
{'chalut': True, ':)': True}
{'give': True, 'minute': True, "i'll": True, 'take': True, 'look': True, ':)': True}
{'listen': True, 'live': True, ':)': True}
{'dog': True, 'guy': True, 'hilarious': True, 'brilliant': True, 'interview': True, 'replay': True, 'iplayer': True, 'late': True, 'funny': True, ':)': True}
{'stats': True, 'day': True, 'arrive': True, '4': True, 'new': True, 'follower': True, 'unfollowers': True, ':)': True, 'via': True}
{'making': True, 'come': True, '10am': True, 'test': True, '11am': True, 'thanks': True, 'unneeded': True, 'stress': True, ':)': True}
{'future': True, 'megamoh': True, '7/29': True, '2015': True, 'happy': True, 'birt

{'tomorrow': True, '#goldcoast': True, ':)': True}
{'like': True, 'way': True, 'say': True, 'gal': True, '#lelomustfall': True, 'beautifull': True, ':)': True}
{'happy': True, 'save': True, 'day': True, ':)': True, 'hope': True, 'enjoy': True, 'meal': True, 'sam': True}
{'thank': True, 'min': True, ':)': True}
{'5g': True, 'liker': True, ':)': True, 'like': True, 'fast': True}
{'like': True, 'morning': True, 'get': True, 'dress': True, 'buy': True, ':)': True, "i'm": True, 'totally': True, 'love': True, '♡': True, '#newdress': True, '#happy': True, '…': True}
{'#ff': True, 'could': True, 'anyone': True, 'resist': True, 'beautiful': True, 'smile': True, ':-)': True, '#quacketyquack': True}
{'u': True, 'mean': True, 'hide': True, 'fots': True, ':p': True}
{'aww': True, 'thankyou': True, ':)': True}
{'ok': True, 'good': True, 'night': True, 'wish': True, 'troye': True, 'ugly': True, 'meet': True, 'today': True, ':)': True, '):': True, 'fun': True, "i'm": True, 'excite': True, 'tmrw': True

In [25]:
import random

positive_dataset = [(tweet_dict, "Positive")
                     for tweet_dict in positive_for_model]

negative_dataset = [(tweet_dict, "Negative")
                     for tweet_dict in negative_for_model]

dataset = positive_dataset + negative_dataset

random.shuffle(dataset)

train_data = dataset[:7000]
test_data = dataset[7000:]

In [26]:
train_data

[({':(': True, 'brienne': True, 'im': True, 'lsh': True, 'meeting': True},
  'Negative'),
 ({'#notanapology': True,
   ':(': True,
   'follow': True,
   'go': True,
   'im': True,
   'nah': True,
   'waitting': True},
  'Negative'),
 ({'..': True,
   '...': True,
   ':(': True,
   'alone': True,
   'back': True,
   'come': True,
   'difficult': True,
   'h': True,
   'mile': True,
   'n': True,
   'someone': True,
   'u': True,
   'walk': True,
   'walking': True},
  'Negative'),
 ({':(': True, 'doin': True, 'ok': True}, 'Negative'),
 ({'5am': True,
   ':(': True,
   'drive': True,
   'finally': True,
   'home': True,
   'since': True},
  'Negative'),
 ({':(': True, 'bad': True, 'miss': True}, 'Negative'),
 ({':(': True, 'gtg': True}, 'Negative'),
 ({'5ever': True, ':-(': True, 'feel': True, 'like': True, 'twitter': True},
  'Negative'),
 ({'#countthecost': True,
   ':-(': True,
   'cake': True,
   'flapjacks': True,
   'forget': True,
   "i'd": True,
   'miss': True,
   'oh': True},
 

In [27]:
from nltk import classify
from nltk import NaiveBayesClassifier
classifier = NaiveBayesClassifier.train(train_data)

print("Accuracy is:", classify.accuracy(classifier, test_data))

print(classifier.show_most_informative_features(10))

Accuracy is: 0
Most Informative Features
None


In [28]:
from nltk.tokenize import word_tokenize

#custom_tweet = "I ordered just once from TerribleCo, they screwed up, never used the app again."
custom_tweet = 'Thank you for sending my baggage to CityX and flying me to CityY at the same time. Brilliant service. #thanksGenericAirline'

custom_tokens = nettoie_donnees(word_tokenize(custom_tweet))

print(classifier.classify(dict([token, True] for token in custom_tokens)))

Negative


In [29]:
stop_wor = stopwords.words('french')

In [30]:
stop_wor

['au',
 'aux',
 'avec',
 'ce',
 'ces',
 'dans',
 'de',
 'des',
 'du',
 'elle',
 'en',
 'et',
 'eux',
 'il',
 'ils',
 'je',
 'la',
 'le',
 'les',
 'leur',
 'lui',
 'ma',
 'mais',
 'me',
 'même',
 'mes',
 'moi',
 'mon',
 'ne',
 'nos',
 'notre',
 'nous',
 'on',
 'ou',
 'par',
 'pas',
 'pour',
 'qu',
 'que',
 'qui',
 'sa',
 'se',
 'ses',
 'son',
 'sur',
 'ta',
 'te',
 'tes',
 'toi',
 'ton',
 'tu',
 'un',
 'une',
 'vos',
 'votre',
 'vous',
 'c',
 'd',
 'j',
 'l',
 'à',
 'm',
 'n',
 's',
 't',
 'y',
 'été',
 'étée',
 'étées',
 'étés',
 'étant',
 'étante',
 'étants',
 'étantes',
 'suis',
 'es',
 'est',
 'sommes',
 'êtes',
 'sont',
 'serai',
 'seras',
 'sera',
 'serons',
 'serez',
 'seront',
 'serais',
 'serait',
 'serions',
 'seriez',
 'seraient',
 'étais',
 'était',
 'étions',
 'étiez',
 'étaient',
 'fus',
 'fut',
 'fûmes',
 'fûtes',
 'furent',
 'sois',
 'soit',
 'soyons',
 'soyez',
 'soient',
 'fusse',
 'fusses',
 'fût',
 'fussions',
 'fussiez',
 'fussent',
 'ayant',
 'ayante',
 'ayantes',


In [31]:
text_tokens = twitter_samples.tokenized('tweets.20150430-223406.json')
text_tokens 

[['RT',
  '@KirkKus',
  ':',
  'Indirect',
  'cost',
  'of',
  'the',
  'UK',
  'being',
  'in',
  'the',
  'EU',
  'is',
  'estimated',
  'to',
  'be',
  'costing',
  'Britain',
  '£',
  '170',
  'billion',
  'per',
  'year',
  '!',
  '#BetterOffOut',
  '#UKIP'],
 ['VIDEO',
  ':',
  'Sturgeon',
  'on',
  'post-election',
  'deals',
  'http://t.co/BTJwrpbmOY'],
 ['RT',
  '@LabourEoin',
  ':',
  'The',
  'economy',
  'was',
  'growing',
  '3',
  'times',
  'faster',
  'on',
  'the',
  'day',
  'David',
  'Cameron',
  'became',
  'Prime',
  'Minister',
  'than',
  'it',
  'is',
  'today',
  '..',
  '#BBCqt',
  'http://t.co…'],
 ['RT',
  '@GregLauder',
  ':',
  'the',
  'UKIP',
  'east',
  'lothian',
  'candidate',
  'looks',
  'about',
  '16',
  'and',
  'still',
  'has',
  'an',
  'msn',
  'addy',
  'http://t.co/7eIU0c5Fm1'],
 ['RT',
  '@thesundaypeople',
  ':',
  "UKIP's",
  'housing',
  'spokesman',
  'rakes',
  'in',
  '£',
  '800k',
  'in',
  'housing',
  'benefit',
  'from',
  'mig

In [38]:
text_nettoye = []

for mot in text_tokens:
    text_nettoye.append(nettoie_donnees(mot, stop_words))
    
text_nettoye

[['rt',
  'indirect',
  'cost',
  'uk',
  'eu',
  'estimate',
  'cost',
  'britain',
  '£',
  '170',
  'billion',
  'per',
  'year',
  '#betteroffout',
  '#ukip'],
 ['video', 'sturgeon', 'post-election', 'deal'],
 ['rt',
  'economy',
  'grow',
  '3',
  'time',
  'fast',
  'day',
  'david',
  'cameron',
  'become',
  'prime',
  'minister',
  'today',
  '..',
  '#bbcqt',
  '…'],
 ['rt',
  'ukip',
  'east',
  'lothian',
  'candidate',
  'look',
  '16',
  'still',
  'msn',
  'addy'],
 ['rt',
  "ukip's",
  'housing',
  'spokesman',
  'rake',
  '£',
  '800k',
  'housing',
  'benefit',
  'migrant',
  '…'],
 ['rt',
  'make',
  'sure',
  'tune',
  '#asknigelfarage',
  'tonight',
  'bbc',
  '1',
  '22:50',
  '#ukip'],
 ['rt',
  'ed',
  'milliband',
  'embarrassment',
  'would',
  'want',
  'represent',
  'uk',
  '#bbcqt',
  'vote'],
 ['rt',
  'ft',
  'back',
  'tories',
  'unrelated',
  'note',
  "here's",
  'photo',
  'ft',
  'leader',
  'writer',
  'jonathan',
  'ford',
  'next',
  'boris',
  

In [39]:
j = 0
for i in text_nettoye:
    print(text[j])
    j = j + 1
    print(i)
    print(classifier.classify(dict([token, True] for token in i)))


RT @KirkKus: Indirect cost of the UK being in the EU is estimated to be costing Britain £170 billion per year! #BetterOffOut #UKIP
['rt', 'indirect', 'cost', 'uk', 'eu', 'estimate', 'cost', 'britain', '£', '170', 'billion', 'per', 'year', '#betteroffout', '#ukip']
Negative
VIDEO: Sturgeon on post-election deals http://t.co/BTJwrpbmOY
['video', 'sturgeon', 'post-election', 'deal']
Negative
RT @LabourEoin: The economy was growing 3 times faster on the day David Cameron became Prime Minister than it is today.. #BBCqt http://t.co…
['rt', 'economy', 'grow', '3', 'time', 'fast', 'day', 'david', 'cameron', 'become', 'prime', 'minister', 'today', '..', '#bbcqt', '…']
Negative
RT @GregLauder: the UKIP east lothian candidate looks about 16 and still has an msn addy http://t.co/7eIU0c5Fm1
['rt', 'ukip', 'east', 'lothian', 'candidate', 'look', '16', 'still', 'msn', 'addy']
Negative
RT @thesundaypeople: UKIP's housing spokesman rakes in £800k in housing benefit from migrants.  http://t.co/GVwb9Rcb4

['rt', 'victorians', 'build', 'leeds', 'town', 'hall', 'leave', 'message', 'roof', 'cameron', 'milliband', 'clegg', '#bbcqt', '…']
Negative
@StuartDillon1 @OwenJones84 No of course not. The only people voting Tory are in England. SNP would block Tories over to Miliband.
['course', 'people', 'vote', 'tory', 'england', 'snp', 'would', 'block', 'tories', 'miliband']
Negative
To what depths has our #electoral behaviour descended? Sadly @oflynnmep is correct
and #TacticalVoting is necessary. https://t.co/u57DjcNjpi
['depth', '#electoral', 'behaviour', 'descend', 'sadly', 'correct', '#tacticalvoting', 'necessary']
Negative
@blairmcdougall @scottishlabour @ScotlandTonight @bbcqt LOL without SNP Labour will not get that chance stale mate!
['lol', 'without', 'snp', 'labour', 'get', 'chance', 'stale', 'mate']
Negative
Make sure you make the right decision when you vote. #GeneralElection #GameofThrones #ELECTION2015 #UKIP http://t.co/3JkQEshik4
['make', 'sure', 'make', 'right', 'decision', 'vote'

Negative
Cameron could show up, have a complete breakdown &amp;/or suggest we all move to the moon, yet Tories would bleat his praises obediently #bbcqt
['cameron', 'could', 'show', 'complete', 'breakdown', 'suggest', 'move', 'moon', 'yet', 'tories', 'would', 'bleat', 'praise', 'obediently', '#bbcqt']
Negative
RT @thhamilton: Unexpectedly, it looks like UKIP want the royal coat of arms taken off the UK passport. http://t.co/ha36sEPClI
['rt', 'unexpectedly', 'look', 'like', 'ukip', 'want', 'royal', 'coat', 'arm', 'take', 'uk', 'passport']
Negative
RT @BristolCWU: Ed Milliband - "We have an economy based on low pay and we are not building enough homes in this Country" @BristolSouthLab …
['rt', 'ed', 'milliband', 'economy', 'base', 'low', 'pay', 'build', 'enough', 'home', 'country', '…']
Negative
@LesLk52 @deboridah86 @Tommo76_ @Carra23 &amp; You can trust the tories? Debt has gone up, sir! Looks like the Sun spewspaper has another victim
['trust', 'tory', 'debt', 'go', 'sir', 'looks', 'l

RT @OwenJones84: David Cameron *refuses* to rule out cutting child benefit. When we all march into the polling booths next week, let’s reme…
['rt', 'david', 'cameron', 'refuse', 'rule', 'cut', 'child', 'benefit', 'march', 'poll', 'booth', 'next', 'week', 'let', '’', 'reme', '…']
Negative
ed miliband is the only one I actually have any faith at all in
['ed', 'miliband', 'one', 'actually', 'faith']
Negative
RT @hermannkelly: #UKIP spokesman .@Steven_Woolfe  attacks hypocrisy of #Labour party  whose meps voted for common EU Asylum policy. http:/…
['rt', '#ukip', 'spokesman', 'attack', 'hypocrisy', '#labour', 'party', 'whose', 'meps', 'vote', 'common', 'eu', 'asylum', 'policy', 'http', ':/', '…']
Negative
RT @jamesosh: Clegg talking crap on tuition fees. He wasn't between 'rock and hard place'. I was in the room when he decided to vote for it…
['rt', 'clegg', 'talk', 'crap', 'tuition', 'fee', 'rock', 'hard', 'place', 'room', 'decide', 'vote', '…']
Negative
@latenightlondon I know UKIP are 

RT @ScotNational: Nobel Prize winning economist: Labour and Tories are completely wrong on austerity http://t.co/GHAeW0wPDP http://t.co/Kpw…
['rt', 'nobel', 'prize', 'win', 'economist', 'labour', 'tories', 'completely', 'wrong', 'austerity', '…']
Negative
RT @MarcherLord1: #bbcqt Miliband:"We will NOT form a coalition with the SNP"
RT for absolute bollocks
FAV for "I'm gullible and totally be…
['rt', '#bbcqt', 'miliband', 'form', 'coalition', 'snp', 'rt', 'absolute', 'bollock', 'fav', "i'm", 'gullible', 'totally', '…']
Negative
RT @Tommy_Colc: FT come out in support of Tories claiming Miliband is "preoccupied w/ inequality". The man who wrote it @sturdyAlex http://…
['rt', 'ft', 'come', 'support', 'tories', 'claim', 'miliband', 'preoccupied', 'w', 'inequality', 'man', 'write', 'http://…']
Negative
RT @blacktriangle1: #NUMPTY #ED #Miliband just declared #war on #Scotland tonight on the #BBC before the entire #UK. That's the truth. He's…
['rt', '#numpty', '#ed', '#miliband', 'declare', '

...

RT @Markfergusonuk: David Cameron says he's hungrier than he was five years ago. So are all of the people reliant on food banks...
['rt', 'david', 'cameron', 'say', "he's", 'hungrier', 'five', 'year', 'ago', 'people', 'reliant', 'food', 'bank', '...']
Negative
RT @CataNigra: #AskNigelFarage conveniently shown as late as possible to avoid UKIP being included in the poll. Farage won. He is honest an…
['rt', '#asknigelfarage', 'conveniently', 'show', 'late', 'possible', 'avoid', 'ukip', 'include', 'poll', 'farage', 'win', 'honest', '…']
Negative
RT @junayed_: Whenever I see Nick Clegg on TV, it just reminds me of this wonderful moment. #BBCQT http://t.co/6SJzqEFdi5
['rt', 'whenever', 'see', 'nick', 'clegg', 'tv', 'remind', 'wonderful', 'moment', '#bbcqt']
Negative
RT @jongaunt: RETWEET PLEASE Brand New Podcast up now Episode 31 BBC Bias against UKIP, Racism, Russell and Ed Love in!
Subscribe http://t.…
['rt', 'retweet', 'please', 'brand', 'new', 'podcast', 'episode', '31', 'bbc', 'bias', 

RT @SonyKapoor: This is hilarious - Apparently the message from the #Tory spin doctors was “Strong, Commanding Performance” #bbcqt http://t…
['rt', 'hilarious', 'apparently', 'message', '#tory', 'spin', 'doctor', '“', 'strong', 'commanding', 'performance', '”', '#bbcqt', '…']
Negative
@LydiaReidYES2 @IndiScoLady @PD3V1NE @rich_falconer @JimForScotland @snp we'll see !
["we'll", 'see']
Negative
RT @craigeylesffc: Poor bbc performance again trying to get @Nigel_Farage  to rush his answers but he still smashed it #UKIP #AskNigelFarage
['rt', 'poor', 'bbc', 'performance', 'try', 'get', 'rush', 'answer', 'still', 'smash', '#ukip', '#asknigelfarage']
Negative
RT @osmart: Aw Miliband, just wait till the Scottish results come in #bbcqt http://t.co/ysyuKWoODI
['rt', 'aw', 'miliband', 'wait', 'till', 'scottish', 'result', 'come', '#bbcqt']
Negative
If either #Milliband  or #Cameron was any good at this then it wouldn't still be a contest
#onaplate #opengoal #likeyoudontevenwantit
['either', '#mi

['rt', 'guardian', 'front', 'page', 'friday', '1', 'may', '2015', 'miliband', 'harden', 'line', 'deal', 'snp']
Negative
RT @b_iffy: Not all immigrants hate UKIP. The people of Bongo Bongo remain ever grateful for the publicity they recieved.
['rt', 'immigrant', 'hate', 'ukip', 'people', 'bongo', 'bongo', 'remain', 'ever', 'grateful', 'publicity', 'recieved']
Negative
RT @wee_things: Ed Milliband message to Scotland so far ;

You WILL NOT get 2nd referendum
You WILL NOT get voice in westminster

Thats UK …
['rt', 'ed', 'milliband', 'message', 'scotland', 'far', 'get', '2nd', 'referendum', 'get', 'voice', 'westminster', 'thats', 'uk', '…']
Negative
Relojes Mk Y Tory Borh Con Caja Lego, Venta al mayor y al detal de relojes Mulco Blue Marine con  ···&gt; http://t.co/FsvToPwbm4 #Anuncios
['relojes', 'mk', 'tory', 'borh', 'con', 'caja', 'lego', 'venta', 'al', 'mayor', 'al', 'detal', 'de', 'relojes', 'mulco', 'blue', 'marine', 'con', '·', '·', '·', '#anuncios']
Negative
RT @eddiebhoyasken: Ge

['rt', 'ukip', 'keep', 'fight', 'even', 'britain', 'vote', 'stay', 'eu', '…']
Negative
RT @Elin_A_Roberts: "What the leader of the opposition has said tonight is highly irresponsible" @LeanneWood on Miliband ruling out any dea…
['rt', 'leader', 'opposition', 'say', 'tonight', 'highly', 'irresponsible', 'miliband', 'rule', 'dea', '…']
Negative
#lastleg Miliband Bullshit https://t.co/dCL20hx5KK
['#lastleg', 'miliband', 'bullshit']
Negative
RT @BBCPolitics: "I'm not going cut your tax credits," Ed Miliband says, and pledges to protect services http://t.co/jsd8Jb1lYA #bbcqt http…
['rt', "i'm", 'go', 'cut', 'tax', 'credit', 'ed', 'miliband', 'say', 'pledge', 'protect', 'service', '#bbcqt', 'http', '…']
Negative
RT @Staircase2: #AskNigelFarage when #UKIP says foreigners are all taking our jobs are they the same foreigners who are all on benefits or …
['rt', '#asknigelfarage', '#ukip', 'say', 'foreigner', 'take', 'job', 'foreigner', 'benefit', '…']
Negative
RT @TeaJunkie1: Lies, Damned Lies a

Negative
@TheUnionScots @KhaleejiKat while romas run around govanhill robbing folk , no cctv until the locals begged HRH sturgeon
['roma', 'run', 'around', 'govanhill', 'rob', 'folk', 'cctv', 'local', 'beg', 'hrh', 'sturgeon']
Negative
RT @cathynewman: Revealed: David Cameron’s father left offshore assets in tax haven of Jersey   http://t.co/leTNS1qlYL #C4News
['rt', 'revealed', 'david', 'cameron', '’', 'father', 'leave', 'offshore', 'asset', 'tax', 'jersey', '#c4news']
Negative
RT @magimay007: @BBCJamesCook @0604Arb1320 Yes, SNP want to break up the UK - why should a party that wants to redistribute wealth across U…
['rt', 'yes', 'snp', 'want', 'break', 'uk', 'party', 'want', 'redistribute', 'wealth', 'across', 'u', '…']
Negative
RT @Coral: Ed Miliband fell off the stage. Just thought you should see —&gt; https://t.co/V5dy0VL0Az
['rt', 'ed', 'miliband', 'fell', 'stage', 'think', 'see', '—']
Negative
RT @PeatWorrier: "A vote for the SNP is. Er. A vote for another referendum we insist H

In [34]:
CLIENT_SECRETS_FILE = "client_secret.json"

SCOPES = ['https://www.googleapis.com/auth/youtube.force-ssl']
API_SERVICE_NAME = 'youtube'
API_VERSION = 'v3'

import google.oauth2.credentials
import os
 
from googleapiclient.discovery import build
from googleapiclient.errors import HttpError
from google_auth_oauthlib.flow import InstalledAppFlow
 
def get_authenticated_service():
    flow = InstalledAppFlow.from_client_secrets_file(CLIENT_SECRETS_FILE, SCOPES)
    credentials = flow.run_console()
    return build(API_SERVICE_NAME, API_VERSION, credentials = credentials)

if __name__ == '__main__':
    os.environ['OAUTHLIB_INSECURE_TRANSPORT'] = '1'
    service = get_authenticated_service()

Please visit this URL to authorize this application: https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=500298203057-ocg8hmq5q31f9cakrm5svokga1m651vn.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fyoutube.force-ssl&state=TqYIMlaE03XxG0Pcn0fWSmt4na9agK&prompt=consent&access_type=offline


KeyboardInterrupt: 

In [184]:
def import_commentaires(youtube, video_id):
  results = youtube.commentThreads().list(
    part="snippet",
    maxResults=100,
    videoId=video_id,
    textFormat="plainText"
  ).execute()
  Lis = []
  for item in results["items"]:
    comment = item["snippet"]["topLevelComment"]
    author = comment["snippet"]["authorDisplayName"]
    text = comment["snippet"]["textDisplay"]
    Lis.append(text)
    print("Commentaire par %s: %s" % (author, text))

  return Lis

dat = import_commentaires(service, "rfscVS0vtbw")

Commentaire par freeCodeCamp.org: Click the "JOIN" button below the video to support freeCodeCamp.org!
Commentaire par Salvation Jane: Can you tutor one on one?
Commentaire par Hermes Lopez: The legend says he's still thinking about where to put the underscore.
Commentaire par Dan Merker: Excellent tutorial. Very useful and easy to understand. Thanks much!
Commentaire par Todd Dupont: thanks
Commentaire par Nightly Tales: 1:29:00 Also a good practice for writing method names you can do this instead of sayhi or say_hi. Like Java you can type sayHi(): just capitalize the second part.
Commentaire par Joan Brunet Verdaguer: no veritcal bar in my keyboard :((
Commentaire par IT Hunt: Nice video. Subscribe on my channel for cybersecurity
Commentaire par Aiden G: just leaving a timestamp 27:00
Commentaire par mahi thakkar: Omg you did hard work!
Commentaire par ꧁xXƤRINCƐXx꧂: well..can anyone help me?.....
so how can i install py launcher?
becuz i accidentally deleted it and the python program

In [185]:
dat

['Click the "JOIN" button below the video to support freeCodeCamp.org!',
 'Can you tutor one on one?',
 "The legend says he's still thinking about where to put the underscore.",
 'Excellent tutorial. Very useful and easy to understand. Thanks much!',
 'thanks',
 '1:29:00 Also a good practice for writing method names you can do this instead of sayhi or say_hi. Like Java you can type sayHi(): just capitalize the second part.',
 'no veritcal bar in my keyboard :((',
 'Nice video. Subscribe on my channel for cybersecurity',
 'just leaving a timestamp 27:00',
 'Omg you did hard work!',
 'well..can anyone help me?.....\nso how can i install py launcher?\nbecuz i accidentally deleted it and the python program that i downloaded from the website\nand when i\'m trying to install python again , the python setup  showing" path not found" .And i can\'t able to access to install py launcher through setup\nso i installed python from microsoft store\nbut in vs code the python is not working even thoug

In [ ]:
donnees = [word_tokenize(i) for i in dat]

In [189]:
donnees

[['Click',
  'the',
  '``',
  'JOIN',
  "''",
  'button',
  'below',
  'the',
  'video',
  'to',
  'support',
  'freeCodeCamp.org',
  '!'],
 ['Can', 'you', 'tutor', 'one', 'on', 'one', '?'],
 ['The',
  'legend',
  'says',
  'he',
  "'s",
  'still',
  'thinking',
  'about',
  'where',
  'to',
  'put',
  'the',
  'underscore',
  '.'],
 ['Excellent',
  'tutorial',
  '.',
  'Very',
  'useful',
  'and',
  'easy',
  'to',
  'understand',
  '.',
  'Thanks',
  'much',
  '!'],
 ['thanks'],
 ['1:29:00',
  'Also',
  'a',
  'good',
  'practice',
  'for',
  'writing',
  'method',
  'names',
  'you',
  'can',
  'do',
  'this',
  'instead',
  'of',
  'sayhi',
  'or',
  'say_hi',
  '.',
  'Like',
  'Java',
  'you',
  'can',
  'type',
  'sayHi',
  '(',
  ')',
  ':',
  'just',
  'capitalize',
  'the',
  'second',
  'part',
  '.'],
 ['no', 'veritcal', 'bar', 'in', 'my', 'keyboard', ':', '(', '('],
 ['Nice',
  'video',
  '.',
  'Subscribe',
  'on',
  'my',
  'channel',
  'for',
  'cybersecurity'],
 ['just

In [209]:
Commentaire = []
for i in donnees:
    Commentaire.append(nettoie_donnees(i, stop_words))

In [191]:
Commentaire

[['click',
  '``',
  'join',
  "''",
  'button',
  'video',
  'support',
  'freecodecamp.org'],
 ['tutor', 'one', 'one'],
 ['legend', 'say', "'s", 'still', 'think', 'put', 'underscore'],
 ['excellent', 'tutorial', 'useful', 'easy', 'understand', 'thanks', 'much'],
 ['thanks'],
 ['1:29:00',
  'also',
  'good',
  'practice',
  'write',
  'method',
  'name',
  'instead',
  'sayhi',
  'say_hi',
  'like',
  'java',
  'type',
  'sayhi',
  'capitalize',
  'second',
  'part'],
 ['veritcal', 'bar', 'keyboard'],
 ['nice', 'video', 'subscribe', 'channel', 'cybersecurity'],
 ['leave', 'timestamp', '27:00'],
 ['omg', 'hard', 'work'],
 ['well..can',
  'anyone',
  'help',
  '...',
  '..',
  'install',
  'py',
  'launcher',
  'becuz',
  'accidentally',
  'delete',
  'python',
  'program',
  'download',
  'website',
  "'m",
  'try',
  'install',
  'python',
  'python',
  'setup',
  'show',
  "''",
  'path',
  'find',
  "''",
  '.and',
  'ca',
  "n't",
  'able',
  'access',
  'install',
  'py',
  'launc

In [192]:
j = 0
for i in Commentaire:
    print(donnees[j])
    j = j + 1
    print(i)
    print(classifier.classify(dict([token, True] for token in i)))

['Click', 'the', '``', 'JOIN', "''", 'button', 'below', 'the', 'video', 'to', 'support', 'freeCodeCamp.org', '!']
['click', '``', 'join', "''", 'button', 'video', 'support', 'freecodecamp.org']
Positive
['Can', 'you', 'tutor', 'one', 'on', 'one', '?']
['tutor', 'one', 'one']
Negative
['The', 'legend', 'says', 'he', "'s", 'still', 'thinking', 'about', 'where', 'to', 'put', 'the', 'underscore', '.']
['legend', 'say', "'s", 'still', 'think', 'put', 'underscore']
Negative
['Excellent', 'tutorial', '.', 'Very', 'useful', 'and', 'easy', 'to', 'understand', '.', 'Thanks', 'much', '!']
['excellent', 'tutorial', 'useful', 'easy', 'understand', 'thanks', 'much']
Positive
['thanks']
['thanks']
Positive
['1:29:00', 'Also', 'a', 'good', 'practice', 'for', 'writing', 'method', 'names', 'you', 'can', 'do', 'this', 'instead', 'of', 'sayhi', 'or', 'say_hi', '.', 'Like', 'Java', 'you', 'can', 'type', 'sayHi', '(', ')', ':', 'just', 'capitalize', 'the', 'second', 'part', '.']
['1:29:00', 'also', 'good', 